In [26]:
from community import community_louvain
import matplotlib.pyplot as plt
import networkx as nx
import math
import numpy as np
import plotly.graph_objects as go
import networkx as nx

In [27]:
def draw_graph(G, pos, degree_dict, quantiles, title):
    colorlist = [
        "#79E789",  # 浅绿色
        "#C3E8E5",  # 浅青色
        "#FDD56A",  # 金黄色
        "#E74C3C",  # 砖红色
        "#FF0000",  # 纯红色
    ]

    degree_values = degree_dict.values()
    quantile_vales = [np.percentile(list(degree_values), q) for q in quantiles]
    def get_color(node):
        degree = degree_dict[node]
        for i, q in enumerate(quantile_vales):
            if degree <= q:
                return colorlist[i]
        return colorlist[-1]
    
    def get_size(node):
        degree = degree_dict[node]
        for i, q in enumerate(quantile_vales):
            if degree <= q:
                return 7 + 2 * i
        return 7 + 2 * len(quantile_vales)

    edge_x = []
    edge_y = []

    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.append(x0)
        edge_x.append(x1)
        edge_x.append(None)
        edge_y.append(y0)
        edge_y.append(y1)
        edge_y.append(None)

    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')
    
    node_x = []
    node_y = []
    colors = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        colors.append(get_color(node))

    # 创建节点的可视化
    node_trace = go.Scatter(
        x=node_x,
        y=node_y,
        mode='markers',
        hoverinfo='text',
        marker=dict(
            size=[get_size(node) for node in G.nodes()],
            color=colors,  # 设置节点的颜色
            line=dict(width=0)
        )
    )

    # 添加节点的悬浮信息
    node_text = [f'Node {node}' for node in G.nodes()]
    node_trace.text = node_text

    # 绘制图形
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title=title,
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=0, l=0, r=0, t=40),
                        xaxis=dict(showgrid=False, zeroline=False),
                        yaxis=dict(showgrid=False, zeroline=False))
                    )

    fig.update_layout(
        plot_bgcolor='white',      # 去除绘图区背景
        paper_bgcolor='white', 
    )

    fig.write_image(f"./figure/{title}.pdf", format="pdf")
    fig.show()


In [28]:

quantiles = [50, 75, 90]

# degree_centrality
def degree(G, pos):
    degree_dict = nx.degree_centrality(G)
    draw_graph(G, pos, degree_dict, quantiles, title="Degree Centrality")
    return True

# eigenvector_centrality
def eigen(G, pos):
    degree_dict = nx.eigenvector_centrality(G)
    draw_graph(G, pos, degree_dict, quantiles, title="Eigenvector Centrality")
    return True


# Katz_centrality
def katz(G, alpha, pos, beta = 1):
    degree_dict = nx.katz_centrality(G, alpha, beta)
    draw_graph(G, pos, degree_dict, quantiles, title="Katz Centrality")
    return True

# pagerank_centrality
def pagerank(G, pos, alpha = 0.85):
    degree_dict = nx.pagerank(G, alpha)
    draw_graph(G, pos, degree_dict, quantiles, title="Pagerank Centrality")
    return True

# betweenness_centrality
def between(G, pos):
    degree_dict = nx.betweenness_centrality(G)
    draw_graph(G, pos, degree_dict, quantiles, title="Betweenness Centrality")
    return

# closeness_centrality
def close(G, pos):
    degree_dict = nx.closeness_centrality(G)
    draw_graph(G, pos, degree_dict, quantiles, title="Closeness Centrality")
    return

In [29]:
# load the karate club graph
G = nx.read_edgelist('../facebook_combined.txt', nodetype=int)


In [30]:
# G = nx.karate_club_graph()
partition = community_louvain.best_partition(G)
subnode = []
for i in partition.keys():
    if partition[i] == 5:
        subnode.append(i)
G = G.subgraph(subnode)

pos = nx.spring_layout(G, k=1.3, iterations=100)

degree(G, pos)


eigen(G, pos)

w, v = np.linalg.eig(nx.to_numpy_array(G))
rho = max(abs(w))
alpha = 0.85/rho
katz(G, alpha, pos)

pagerank(G, pos)

between(G, pos)

close(G, pos)
